In [ ]:
import numpy as np
import collections
import itertools

# Algorithme Apriori

Dans ce TP, nous allons implémenter l'algorithme Apriori qui permet d'extraire des régles d'association à partir d'une base de données de transactions.
Nous commencerons par quelques rappels de Python, et notamment la manipulation d'ensembles.

## 1. Les ensembles en Python

Un ensemble est une collection d'objets qui ne peut pas contenir de doublons.

In [ ]:
# création d'un ensemble
s = {1, 2, 10}

print(type(s))
print(s)

In [ ]:
# attention, il ne faut pas confondre la syntaxe de création
# d'un dictionnaire avec celle d'un ensemble

# création d'un dictionnaire
d = {1: "a", 2: "b"}
print(type(d))
print(d)

In [ ]:
# attention, pour créer un ensemble vide, on ne peut pas utiliser {},
# cela créé un dictionnaire
d = {}
print(type(d))

# création d'un ensemble vide
s = set()
print(type(s))
print(s)

In [ ]:
# on peut ajouter des éléments à un ensemble
s = set()
print(s)

s.add(1)
s.add(10)
print(s)

In [ ]:
# si on ajoute deux fois le même élément,
# il n'apparait qu'une fois dans l'ensemble
s = set()
s.add(1)
s.add(1)
print(s)

Nous allons maintenant décrire quelques opérations possibles sur les ensembles.
Vous pouvez consulter la documentation pour plus d'information : https://docs.python.org/3/library/stdtypes.html#set-types-set-frozenset

In [ ]:
# len(s) retourne le nombre d'élément dans l'ensemble s
s = {"maison", "jardin", "appartement"}
print(s)

In [ ]:
# parcourir les éléments d'un ensemble
s = {"maison", "jardin", "appartement"}
for i in s:
    print(i)

In [ ]:
# soit deux ensembles s1 et s2
# l'union de s1 et s2 est l'ensemble qui contient
# tous les éléments de s1 et de s2
# Attention : le résultat est un ensemble, donc sans doublon !

s1 = {"maison", "jardin", "appartement"}
s2 = {"route", "jardin"}

# fait l'union entre s1 et s2
# à noter ni s1 ni s2 ne sont modifié
# il est aussi possible de faire s2.union(s1), cette opération est symmétrique
s3 = s1.union(s2)
print(s3)

In [ ]:
# soit deux ensembles s1 et s2
# l'intersection de s1 et s2 est l'ensemble qui contient
# tous les éléments qui apparaissent à la fois dans s1 et dans s2

s1 = {"maison", "jardin", "appartement"}
s2 = {"route", "jardin"}

# fait l'intersection entre s1 et s2
# à noter ni s1 ni s2 ne sont modifié
# il est aussi possible de faire s2.intersection(s1), cette opération est symmétrique
s3 = s1.intersection(s2)
print(s3)

In [ ]:
# il existe également une fonction intersection_update qui modifie
# l'ensemble auquel il est appliqué
# (c'est-à-dire qu'il ne retourne pas un nouvel objet mais modifie un objet)
# Je déconseille fortement d'utiliser cette fonction

s1 = {"maison", "jardin", "appartement"}
s2 = {"route", "jardin"}

# modifie s1 mais pas s2
s1.intersection_update(s2)
print(s1)
print(s2)

In [ ]:
# soit s1 et s2 deux ensembles
# il est possible de construire un ensemble qui contient tous les éléments de s1
# sauf ceux qui sont dans s2 (différence d'ensembles)
# l'opération a une variante _update, mais encore une fois,
# je déconseille l'utilisation de la variante _update

s1 = {"maison", "jardin", "appartement"}
s2 = {"route", "jardin"}

s3 = s1.difference(s2)
print(s3)

# vous pouvez aussi utiliser le signe -
s4 = s1 - s2
print(s4)

Le dernier type d'opération que l'on va voir permettent de tester le contenu d'un ensemble.

In [ ]:
s = {"maison", "jardin", "appartement"}
e1 = "maison"
e2 = "chateau"

# l'opération "in" retourne vrai si un élément est dans un ensemble
print(e1 in s)
print(e2 in s)

In [ ]:
s = {"maison", "jardin", "appartement"}
e1 = "maison"
e2 = "chateau"

if e1 in s:
    print("e1 est dans s")
if e2 in s:
    print("e2 est dans s")
    
# on peut aussi faire un test "n'est pas"

if e1 not in s:
    print("e1 n'est pas dans s")
if e2 not in s:
    print("e2 n'est pas dans s")

In [ ]:
s1 = {"maison", "jardin", "appartement"}
s2 = {"maison", "jardin"}
s3 = {"maison", "route"}

# test si s2 (ou s3) est un sous ensemble de s1,
# c'est à dire si tous les élément de s2 sont également dans s1
print(s2.issubset(s1))
print(s3.issubset(s1))

In [ ]:
s1 = {"maison", "jardin", "appartement"}
s2 = {"maison", "jardin"}
s3 = {"maison", "route"}

# on peut également tester si un ensemble est contient un autre
print(s1.issuperset(s2))
print(s1.issuperset(s3))

Un ensemble est un objet mutable, il est possible de le modifier pour y ajouter (ou y supprimer) des éléments.
Si cela est pratique, il y a un inconvénient majeur : il n'est pas possible d'avoir des ensembles d'ensembles et d'utiliser un ensemble comme clé d'un dictionnaire.

Pour corriger ce problème, il existe un type `frozenset` qui, comme son nom l'indique, représente un ensemble figé (qu'il n'est pas possible de modifier). On peut alors avoir un ensemble de frozensets et utiliser un frozenset comme clé d'un dictionnaire.

In [ ]:
s = {1, 2}
d = dict()

# si on essaie d'utiliser s comme clé, cela va produire une erreur
d[s] = 10
print(d)

In [ ]:
s = {1, 2}
d = dict()

# par contre avec un frozenset cela fonctionne !
s2 = frozenset(s2)
print(type(s2))

d[s2] = 10
print(d)

In [ ]:
s = {1, 2}
s2 = frozenset(s)

# il n'est pas possible d'ajouter des éléments dans un frozenset,
# cela va générer une erreur
s2.add(3)

# 2. Les compteurs en Python

Il est souvent utile de compter le nombre de fois que l'on rencontre différent élément.
La classe `collections.Counter` permet de faire cela simplement.

Le fonctionnement est simple :

1. on créé un objet de type `collections.Counter`
2. pour ajouter

L'avantage par rapport à l'utilisation d'un dictionnaire est d'une part que l'on a pas besoin d'initialiser à 0 le comptage,
et d'autres part qu'il existe des fonctions pour manipuler le résultat du comptage (pas utile dans ce TP) : https://www.ladepeche.fr/2023/11/03/prendre-lavion-pour-aller-faire-ses-courses-en-pologne-deux-anglais-demontrent-que-cest-moins-cher-que-le-supermarche-du-coin-11558504.php

**Remarque qui sera importante pour la suite**: vous ne pouvez pas compter les occurences d'ensembles, mais par contre vous pouvez compter les occurences de `frozenset` !

In [ ]:
l = ["a", "b", "a", "c", "c", "a"]

counter = collections.Counter()

# on itère sur les élèments de l
for e in l:
    # on incrémente la valeur associé à e
    # Note : on a pas eu besoin d'initialiser à 0 !
    counter[e] += 1

# affiche le counter
print(counter)

In [ ]:
# Même chose que ci-dessus mais avec un dictionnaire,
# moins pratique :(

l = ["a", "b", "a", "c", "c", "a"]
d = dict()

for e in l:
    if e not in d:
        d[e] = 0  # obligé d'initialisé si pas présent
    d[e] += 1

# affiche le counter
print(d)

Une fois le compteur créé, il est possible de le manipuler comme un dictionnaire.

In [ ]:
l = ["a", "b", "a", "c", "c", "a"]
counter = collections.Counter()
for e in l:
    counter[e] += 1

# parcours par couple clé/valeur
for k, v in counter.items():
    print("Le caractère '" + k + "' a été vu " + str(v) + " fois.")

In [ ]:
l = ["a", "b", "a", "c", "c", "a"]
counter = collections.Counter()
for e in l:
    counter[e] += 1

# créé un ensemble qui ne contient que les caractères qui ont été vu au moins deux fois
s = set()
for k, v in counter.items():
    if v >= 2:
        s.add(k)
print(s)

## 3. Algorithme Apriori

Nous allons maintenant implémenter l'algorithme Apriori. Pour cela, nous implémentons chaque partie de l'algorithme indépendament, avant de combiner le tout.
À noter que l'implémentation que nous allons faire n'est pas très optimisée, mais ce n'est pas grave.
L'objectif est simplement de faire un peu de Python et de comprendre le fonctionnement de l'algorithme.

Pour commencer, nous utiliser un jeu de données factices, qui va vous permettre de tester si vos implémentation sont correctes ou non. Pour chaque fonction, il y a ensemble de test qui permettent de vérifier que tout fonctionne bien,

In [ ]:
def build_simple_dataset():
    return [
        {"tomates", "beurre"},
        {"tomates", "pain", "fromage"},
        {"tomates", "pain"},
        {"pain", "fromage", "beurre"},
        {"confiture", "pain"},
        {"confiture", "pain", "fromage"},
        {"tomates", "beurre"},
        {"pain", "fromage", "beurre"},
    ]

In [ ]:
transactions = build_simple_dataset()

# la base de données est une liste de transactions,
# chaque transaction est un ensemble
print(transactions)

### Extraction des candidats de longueur 1

Nous commençons par créer tous les candidats de taille 1 (c'est-à-dire les candidats ne contenant qu'un seul élément).
On ne filtre pas par fréquence pour le moment.

Deux remarques :

- la fonction doit retourner un ensemble
- un candidat est lui même un ensemble, les candidats seront donc des instances de type frozenset

In [ ]:
def build_unary_candidates(transactions):
    ret = set()
    
    # TODO TODO TODO
    
    return ret

In [ ]:
transactions = build_simple_dataset()
print(build_unary_candidates(transactions))

In [ ]:
# test le type du retour
transactions = build_simple_dataset()
candidates = build_unary_candidates(transactions)

# la fonction doit retourner un ensemble
assert type(candidates) == set
# l'ensemble doit contenir des éléments de type frozenset
assert all(type(c) == frozenset for c in candidates)

# test qu'on a bien le bon résultat
goal = {frozenset({'pain'}), frozenset({'confiture'}), frozenset({'fromage'}), frozenset({'tomates'}), frozenset({'beurre'})}
assert candidates == goal

### Extension de candidats

Nous allons maintenant implémenter la fonction qui étends un ensemble de candidats pour créer des candidats (strictement) plus grands.
Comme précédemment, pour le moment nous ne filtrons pas par fréquence.

La fonction prends deux arguments :

- `candidates` : l'ensemble des candidats à étendre
- `extensions` : l'ensemble des extensions possibles (on suppose que chaque extension a une taille de 1, mais cela ne change rien au niveau de l'implémentation)

Attention, dans l'exemple 1 ci-dessous, si on fait l'union de {"a"} (candidat) et {"a"} (extension possible), le résultat est l'ensemble {"a"}, donc il n'est pas ajouté au résultat car sa taille n'est pas strictement supérieure à celle du candidat.
Pour filtrer cela, il suffit de tester si une extension est un sous-ensemble du candidat considéré ou non.

Exemple 1 :

- candidates = { {"a"}, {"b"} }
- extensions = { {"a"}, {"c"} }
- résultat de l'extension = { {"a", "c"}, {"b", "a"}, {"b", "c"} }

Exemple 2 :

- candidates = { {"a", "b"}, {"b", "d"} }
- extensions = { {"a"}, {"c"} }
- résultat de l'extension = { {"a", "b", "c"}, {"b", "d", "a"}, {"b", "d", "c"} }

In [ ]:
def extend_candidates(candidates, extensions):
    # list2 ne doit contenir que des candidats contenant un seul élément
    assert all(len(c) == 1 for c in extensions)
    
    ret = set()  # ensemble des candidats après la fusion
    
    # TODO TODO TODO
    
    return ret

In [ ]:
# test l'exemple 1
s1 = { frozenset({"a"}), frozenset({"b"}) }
s2 = { frozenset({"a"}), frozenset({"c"}) }
r = extend_candidates(s1, s2)

assert r == { frozenset({"a", "c"}), frozenset({"b", "a"}), frozenset({"b", "c"}) }

In [ ]:
# test l'exemple 2
s1 = { frozenset({"a", "b"}), frozenset({"b", "d"}) }
s2 = { frozenset({"a"}), frozenset({"c"}) }
r = extend_candidates(s1, s2)

assert r == { frozenset({"a", "b", "c"}), frozenset({"b", "d", "a"}), frozenset({"b", "d", "c"}) }

### Filtrage par support minimum

Nous allons maintenant implémenter la fonction qui filtre les candidats par rapport à leur support.

Les arguments de la fonction sont :

- `transactions` : la base de données de transactions
- `candidates` : l'ensemble des candidats à tester
- `support_threshold` : le support minimum que doivent avoir les candidats pour être retournés par le filtre (en %! par exemple `support_threshold=0.5` signifie que les candidats doivent apparaitre dans au moins 50% des transactions)

La fonction doit retourner l'ensemble des candidats dont le support est supérieur ou égale à `support_threshold`.

In [ ]:
def prune_candidates(transactions, candidates, support_threshold):
    counter = collections.Counter()
    
    # TODO TODO TODO

In [ ]:
# quelques tests...

transactions = build_simple_dataset()
candidates = build_unary_candidates(transactions)

r1 = prune_candidates(transactions, candidates, support_threshold=0.)
assert r1 == candidates

r2 = prune_candidates(transactions, candidates, support_threshold=0.2)
assert r2 == {frozenset({'confiture'}),
             frozenset({'pain'}),
             frozenset({'fromage'}),
             frozenset({'tomates'}),
             frozenset({'beurre'})
}

r3 = prune_candidates(transactions, candidates, support_threshold=0.5)
assert r3 == {frozenset({'pain'}), frozenset({'fromage'}), frozenset({'beurre'}), frozenset({'tomates'})}

r4 = prune_candidates(transactions, candidates, support_threshold=0.7)
assert r4 == {frozenset({'pain'})}

r5 = prune_candidates(transactions, candidates, support_threshold=0.8)
assert r5 == set()

### Génération de tous les candidats ayant un support minmum

Maintenant, l'objectif est de générer tous les candidats qui ont un support minimum dans la base de données.
Pour cela, nous construisons la liste `candidates_by_size` tel que :

- `candidates_by_size[0]` est l'ensemble des candidats de taille 1 dont le support est supérieur ou égal à `support_threshold`
- `candidates_by_size[1]` est l'ensemble des candidats de taille 2 dont le support est supérieur ou égal à `support_threshold`
- `candidates_by_size[2]` est l'ensemble des candidats de taille 3 dont le support est supérieur ou égal à `support_threshold`
- `candidates_by_size[3]` est l'ensemble des candidats de taille 4 dont le support est supérieur ou égal à `support_threshold`
- etc etc

On s'arrête lorsque l'ensemble des candidats est pour la dernière taille considéré est l'ensemble vide (i.e. pas de candidats pour cette taille là).

Ensuite, la fonction retourne simplement l'ensemble de tous les candidats de taille strictement supérieur à 1 (cette étape est déjà implémenté).

In [ ]:
def generate_candidates(transactions, support_threshold):
    candidates_by_size = list()
    
    # on commence par les candidats de taille 1, facile !
    unary_candidates = build_unary_candidates(transactions)
    candidates_by_size.append(prune_candidates(transactions, unary_candidates, support_threshold))
    
    # maintenant, c'est à vous de jouer, en utilisant les fonctions définies précédemment !
    # Note : une boucle while peut être pratique.
    
    # TODO TODO TODO

    # On ne retourne pas les ensembles en début de liste (candidats de taille 1)
    return set(itertools.chain(*candidates_by_size[1:]))

In [ ]:
# test

assert generate_candidates(build_simple_dataset(), 0.5) == {frozenset({'fromage', 'pain'})}

assert generate_candidates(build_simple_dataset(), 0.2) == {frozenset({'confiture', 'pain'}),
             frozenset({'beurre', 'tomates'}),
             frozenset({'fromage', 'pain'}),
             frozenset({'beurre', 'fromage'}),
             frozenset({'beurre', 'fromage', 'pain'}),
             frozenset({'pain', 'tomates'}),
             frozenset({'beurre', 'pain'})
}

### Génération des règles

Nous allons maintenant, à partir d'un candidat $C$ (un ensemble d'items), générer l'ensemble des règles $A \implies B$ qui une confiance minimum.

Quelques précision :

- Étant donné le candidat $C$, les régles $A \implies B$ doivent être définies tel que $A \cup B = C$ et $A \cap B = \emptyset$
- Dans la règle $A \implies B$, $A$ est l'antécédent et $B$ le conséquent
- Pour simplifier le problème, nous nous nous limitons aux cas où $|B| = 1$, c'est-à-dire où le conséquent n'est composé que d'un seul item.

Par exemples, si $C = \{\text{"pain"}, \text{"beurre"}, \text{"fromage"}\}$,
les règlès à considérer sont :

- $\{\text{"beurre"}, \text{"fromage"}\} \implies \{ \text{"pain"} \}$
- $\{\text{"pain"}, \text{"fromage"}\} \implies \{ \text{"beurre"} \}$
- $\{\text{"pain"}, \text{"beurre"}\} \implies \{ \text{"fromage"} \}$

Il faut alors retourner les règles parmis celles-ci dont la confiance est d'au minimum `confidence_threshold`.

In [ ]:
def generate_rules_from_candidate(transactions, candidate, confidence_threshold):
    rules = list()
    # pour ajouter une régle dans la list, on utilisera la fonction suivante :
    # rules.append((
    #    antecedents,  # => doit être un ensemble
    #    consequent    # => doit être un unique élément
    # ))
    # une règle est donc représentée ici comme un tuple (antécédents, conséquent)
    
    
    # TODO TODO TODO

    return rules

In [ ]:
# Doit afficher :
# [({'beurre'}, 'pain')]
generate_rules_from_candidate(build_simple_dataset(), {"pain", "beurre"}, 0.5)

In [ ]:
# Doit afficher :
# []
generate_rules_from_candidate(build_simple_dataset(), {"pain", "beurre"}, 0.8)

In [ ]:
# Doit afficher :
# [({'beurre', 'fromage'}, 'pain'),
# ({'beurre', 'pain'}, 'fromage'),
# ({'fromage', 'pain'}, 'beurre')]
generate_rules_from_candidate(build_simple_dataset(), {"pain", "fromage", "beurre"}, 0.5)

In [ ]:
# Doit afficher :
# [({'beurre', 'fromage'}, 'pain'), ({'beurre', 'pain'}, 'fromage')]
generate_rules_from_candidate(build_simple_dataset(), {"pain", "fromage", "beurre"}, 0.8)

### Algorithme a priori

Maintenant, à vous de combiner le tout pour implémenter l'algorithme apriori pour l'extraction de règles d'association !

In [ ]:
def apriori(transactions, support_threshold, confidence_threshold):
    
    # TODO TODO TODO
    

In [ ]:
def print_rules(rules):
    for k, v in rules:
        print("%s => %s" % (" + ".join(k), v))

In [ ]:
# Exemple d'utilisation
print_rules(apriori(build_simple_dataset(), 0.5, 0.8))

**TODO:**
Tester l'algorithme en faisant varier `support_threshold` et `confidence_threshold`. Qu'observez-vous ?
Essayer de comparer et d'interpréter les résultats.

Par exemple, comparez :

- `support_threshold=0.5`, `confidence_threshold=0.8`
- `support_threshold=0.2`, `confidence_threshold=0.8`

etc etc.

## 3. Test sur des données plus réalistes

Vous allez maintenant pouvoir tester cette algorithme sur des données un peu plus réalistes ! Les données sont à télécharger sur la page du cours.

Le fichier `vote.arff` contient des informations de vote au congrès américain. Nous avons pour plusieurs personne, leur affiliation (démocrate ou républicain) ainsi que la liste des loies pour lesquels ils et elles ont votés pour.

Qu'observez-vous lorsque vous éxecutez l'algorithme sur ces données ? Est-on satisfait ? Que peut-on en déduire ?

In [ ]:
import scipy.io.arff

In [ ]:
def load_vote_data(path):
    data, metadata = scipy.io.arff.loadarff(path)
    metadata = metadata.names()
    
    transactions = list()
    for row in data:
        t = set()
        for idx, v in enumerate(list(row)[:-1]):
            #print(v)
            if v == b'y':
                t.add(metadata[idx])
        if len(t) > 0:
            t.add(row[-1].decode())
            transactions.append(t)
    return transactions
    
vote_transactions = load_vote_data("./vote.arff")
print(len(vote_transactions))

In [ ]:
print_rules(apriori(vote_transactions, 0.2, 0.8))